## Example using constrained GP model
This is the code used to produce the first example in the paper _'Gaussian processes with linear operator inequality constraints'_, https://arxiv.org/abs/1901.03134

### Imports

In [1]:
### Basic imports ###
import sys, os

# For plotting
import plotly
import plotly.plotly as pltly
import plotly.graph_objs as go
import plotly.offline as pltlyoff
from IPython.display import display, HTML

# This is for plotting as static images (to show on e.g. GitHub)
import plotly.io as pio
from IPython.display import Image

# Numerics
import numpy as np
import scipy as sp
import itertools
import pyDOE

### Custom files ###

# Path to custom plotly module 'GPPlotly' for plotting 
# can be downloaded at https://github.com/cagrell/gp_plotly
dir_GPPlotly = 'C:\\Data\\git repos\\gp_plotly\\'
sys.path.append(dir_GPPlotly) 

# Path to the constrained GP moule 
# can be downloaded at https://github.com/cagrell/gp_constr
dir_gp_constr = 'C:\\Data\\git repos\\gp_constr\\'
sys.path.append(dir_gp_constr) 

# Import
from GPPlotly.plottingfunctions import PlotGP2d, add_traces_to_fig
from GPConstr.model import kernel_RBF, GPmodel, Constraint

### Setup notebook ###
pltlyoff.init_notebook_mode(connected=True)
print('Python version', sys.version)

Loading constrained GP module from C:\Data\git repos\gp_constr
Loading R wrapper...
Running R from rpy2: R version 3.4.3 (2017-11-30)


Python version 3.6.3 (v3.6.3:2c5fed8, Oct  3 2017, 18:11:49) [MSC v.1900 64 bit (AMD64)]


## 1. Define function for generating synthetic test/training data


In [3]:
# Function to emulate/estimate
def fun(x):
    return (np.arctan(20*x - 10) - np.arctan(-10))/3

## 2. Noiseless regression (emulation)

### 2.1. Generate synthetic training data

In [4]:
# Design data - with noise
n = 50
noise_std = 0.2
x_design = np.random.uniform(0.1, 0.8, n)
y_design = fun(x_design) + np.random.normal(0, noise_std, n)

# For plotting
x_test = np.linspace(0, 1, 500)
y_true = fun(x_test)

### 2.2. Define GP model

In [5]:
# Set up model
ker = kernel_RBF(variance = 0.5, lengthscale = [0.1])
model = GPmodel(kernel = ker, likelihood = 1, mean = 0) 

# Add the training data
model.X_training = x_design.reshape(-1, 1)
model.Y_training = y_design

### 2.2.3. Include constraints

In [6]:
# Helper functions for constraints

def constant_function(val):
    """ Return the constant function"""
    def fun(x):
        return np.array([val]*x.shape[0])
    
    return fun

def fun_UB(x):
    """ Upper bound function """
    return np.log(30*x.flatten() + 1)/3 + 0.1


In [7]:
# Define constraints for bounding the function and its derivative
constr_bounded = Constraint(LB = constant_function(0), UB = fun_UB)
constr_deriv = Constraint(LB = constant_function(0), UB = constant_function(float('Inf')))

In [8]:
# Add constraints to model
model.constr_bounded = constr_bounded
#model.constr_deriv = [constr_deriv] # Add list of constraints for multi-dimensional functions

In [77]:
# Set virtual points manually 
model.reset()
model.constr_bounded.Xv = pyDOE.lhs(n = 1, samples = 20)
#model.constr_deriv[0].Xv = pyDOE.lhs(n = 1, samples = 6)

print(model)

----- GP model ----- 
 mean = 0 
 likelihood = 1 
 kernel: 
   type = RBF 
   input dim = 1 
   lenghtscale = [1.2913355483858397] 
   variance = 0.31798331034722804 
 constraint: 
   f [20] 
   constr_likelihood = 1e-06 
---------------------


In [23]:
# Search for a suitable set of virtual observation locations where the constraint is imposed
df = model.find_XV_subop(bounds = [(0.001, 1)], p_target = 0.9, max_iterations = 100, min_prob_unconstr_xv = -1, i_range = [0, 1], opt_method = 'shgo')

Searching for points XV s.t. P(a - nu < Lf < b + nu) > p_target = 0.9 for Lf = [f, df/dx_1] and nu = 1.2815515655446004e-06 ...
i = 0, XV[1] = [0.001], prob = 0.06707770917345024, acc. rate = 1, optimization time = 0.082 seconds
i = 1, XV[2] = [0.70576103], prob = 0.16443444513500707, acc. rate = 1, optimization time = 0.127 seconds
i = 1, XV[3] = [0.86461883], prob = 0.10399747924207722, acc. rate = 0.011029400397547415, optimization time = 0.087 seconds
i = 1, XV[4] = [1.], prob = 0.11190795786022556, acc. rate = 0.0011362653392191274, optimization time = 0.115 seconds
i = 1, XV[5] = [0.07769063], prob = 0.3739528633351403, acc. rate = 0.00012866517458458106, optimization time = 0.047 seconds
i = 1, XV[6] = [0.001], prob = 0.26328804495282315, acc. rate = 4.8422805542267085e-05, optimization time = 0.031 seconds
i = 0, XV[7] = [1.], prob = 0.40530792358397466, acc. rate = 1.2785713725086784e-05, optimization time = 0.066 seconds
DONE - Found 7 points. Min. constraint prob = 0.9928626

In [24]:
# Search for a suitable set of virtual observation locations where the constraint is imposed
df = model.find_XV_subop(bounds = [(0.001, 1)], p_target = 0.9, max_iterations = 100, min_prob_unconstr_xv = -1, i_range = [0, 1], opt_method = 'differential_evolution')

Searching for points XV s.t. P(a - nu < Lf < b + nu) > p_target = 0.9 for Lf = [f, df/dx_1] and nu = 1.2815515655446004e-06 ...
i = 1, XV[1] = [0.16586802], prob = 0.005485640736289899, acc. rate = 5.326867270865082e-06, optimization time = 0.891 seconds
i = 1, XV[2] = [0.03588971], prob = 0.16216478336610227, acc. rate = 5.326867270865082e-06, optimization time = 0.470 seconds
i = 1, XV[3] = [0.12839922], prob = 0.22051407276952223, acc. rate = 3.372173889087223e-09, optimization time = 0.570 seconds
i = 1, XV[4] = [0.6217095], prob = 0.31031729215927517, acc. rate = 7.505639863405265e-10, optimization time = 0.379 seconds
i = 1, XV[5] = [0.76816564], prob = 0.07335581764949937, acc. rate = 2.2517296947514974e-10, optimization time = 0.339 seconds
i = 1, XV[6] = [0.93072666], prob = 0.11135328452645739, acc. rate = 1.6943330042203147e-11, optimization time = 0.370 seconds
i = 1, XV[7] = [0.65886169], prob = 0.4511190005622238, acc. rate = 2.2763547527332414e-12, optimization time = 0.

In [ ]:
# Optimize unconstrained
#model.optimize(include_constraint = False, fix_likelihood = True)
#print(model)

In [86]:
# Plot unconstrained GP
mean_unconstr, cov_unconstr = model.calc_posterior_unconstrained(x_test.reshape(-1, 1), full_cov = True)
mean_unconstr = np.array(mean_unconstr).flatten()
var_unconstr = np.diagonal(cov_unconstr)

num_samples = 30
show_samplepaths = True
samplepaths_unconstr = []
if show_samplepaths: samplepaths_unconstr = np.random.multivariate_normal(mean_unconstr, cov_unconstr, num_samples).T

fig_unconstr_1 = PlotGP2d(x_mean = x_test, mean = mean_unconstr, var = var_unconstr,
                        x_obs = model.X_training[:,0], y_obs = model.Y_training, 
                        num_std = 1.2815,
                        x_true = x_test, y_true = y_true,
                        samplepaths = samplepaths_unconstr,
                        title = 'Unconstrained GP', xrange = [0, 1], yrange = [-1.7, 1.7], smoothing = True)

trace_UB = go.Scatter(x = x_test, y = model.constr_bounded.UB(x_test), mode = 'lines', name = 'Upper bound', line = dict(color = ('rgb(0, 0, 0)'), shape = 'spline', width = 1))
trace_LB = go.Scatter(x = x_test, y = model.constr_bounded.LB(x_test), mode = 'lines', name = 'Lower bound', line = dict(color = ('rgb(0, 0, 0)'), shape = 'spline', width = 1))

fig_unconstr_1 = add_traces_to_fig(fig_unconstr_1, [trace_UB, trace_LB])

pltlyoff.iplot(fig_unconstr_1, filename='')

..Running calculation of K_w ... SKIP - (cached)
..Running calculation of Cholesky factor for K_w ... SKIP - (cached)
..Calculating f* | Y ... DONE - Total time: 0.026 seconds


In [91]:
# Plot model with both constraints

mean, var, perc, mode, samples = model.calc_posterior_constrained(x_test.reshape(-1, 1), compute_mode = False, num_samples = 10000, save_samples = 30, algorithm = 'minimax_tilting', resample = False)

mean = np.array(mean).flatten()
p_lower = perc[0]
median = perc[1]
p_upper = perc[2]
p_label = '[p{}, p{}]'.format(10, 90)

samplepaths_Z = np.array(samples)

fig_both = PlotGP2d(x_mean = x_test, mean = mean,
                        x_obs = model.X_training[:,0], y_obs = model.Y_training, 
                        p_lower = p_lower, p_upper = p_upper, p_label = p_label,
                        samplepaths =  samplepaths_Z,
                        x_true = x_test, y_true = y_true,
                        title = 'Both constraints', xrange = [0, 1], yrange = [-1.7, 1.7], smoothing = True)

trace_UB = go.Scatter(x = x_test, y = model.constr_bounded.UB(x_test), mode = 'lines', name = 'Upper bound', line = dict(color = ('rgb(0, 0, 0)'), shape = 'spline', width = 1))
trace_LB = go.Scatter(x = x_test, y = model.constr_bounded.LB(x_test), mode = 'lines', name = 'Lower bound', line = dict(color = ('rgb(0, 0, 0)'), shape = 'spline', width = 1))
trace_XV_bounded = go.Scatter(x = model.constr_bounded.Xv.flatten(), y = np.zeros(model.constr_bounded.Xv.shape[0]), mode = 'markers', name = 'Xv - boundedness', marker = dict(symbol = 'line-ns-open', color = ('rgb(0, 0, 0)')))
#trace_XV_mon = go.Scatter(x = model.constr_deriv[0].Xv.flatten(), y = np.zeros(model.constr_deriv[0].Xv.shape[0]), mode = 'markers', name = 'Xv - monotonicity', marker = dict(symbol = 'x-thin-open', color = ('rgb(0, 0, 0)')))

#fig_both = add_traces_to_fig(fig_both, [trace_UB, trace_LB, trace_XV_bounded, trace_XV_mon])
fig_both = add_traces_to_fig(fig_both, [trace_UB, trace_LB, trace_XV_bounded])

pltlyoff.iplot(fig_both, filename='')


..Running calculation of K_w ... SKIP - (cached)
..Running calculation of Cholesky factor for K_w ... SKIP - (cached)
..Running preparation step 1 - dependence on (XS, X) ... DONE - time: 0.031 seconds
..Running preparation step 2 - dependence on (XV, X) ... DONE - time: 0.000 seconds
..Running preparation step 3 - dependence on (XS, XV, X) ... DONE - time: 0.000 seconds
..sampling 10000 times from truncated constraint distribution C~|C, Y DONE - time: 0.436 seconds
..sampling 10000 times from constrained GP f*|C, Y DONE - time: 0.818 seconds
..computing statistics from samples DONE - time: 0.208 seconds
 DONE - Total time: 1.492 seconds


## Plot likelihood

In [51]:
# Some helper functions
def Create_meshdata(plotfun, x_range, y_range, *args, **kwargs):
    """
    Function for creating meshgrid data for surface plotting.
    Inputs:
        plotfun - function of (x, y, *args, **kwargs)
        x_range, y_range
    Outputs:
        X, Y - meshgrid of x_range and y_range
        Z - plotfun(X, Y, *args, **kwargs)
    """
    
    # Create meshgrid
    X, Y = np.meshgrid(x_range, y_range)
    
    # Evaluate function
    vfun = np.vectorize(plotfun)
    Z = [vfun(x, y, *args, **kwargs) for x, y in zip(X, Y)]
    
    return X, Y, Z

def loglik_unconstr(x, y):
    """
    x = kernel lengthscale
    y = kernel variance
    """
    model.kernel.variance = y
    model.kernel.lengthscale = [x]
    model.reset()
    return model._loglik_unconstrained()

def loglik_constr(x, y):
    """
    x = kernel lengthscale
    y = kernel variance
    """
    model.kernel.variance = y
    model.kernel.lengthscale = [x]
    model.reset()
    
    v_loglik_unconstr = model._loglik_unconstrained() # P(Y)
    v_loglik_constr = np.log(model.constrprob_Xv(posterior = True, algorithm = 'minimax_tilting', n = 100)) # P(C|Y)
            
    return v_loglik_unconstr + v_loglik_constr # P(Y, C)

def loglik_constr_cond(x, y):
    """
    x = kernel lengthscale
    y = kernel variance
    """
    model.kernel.variance = y
    model.kernel.lengthscale = [x]
    model.reset()
    
    v_loglik_unconstr = model._loglik_unconstrained() # P(Y)
    v_loglik_constr_cond = np.log(model.constrprob_Xv(posterior = False, algorithm = 'minimax_tilting', n = 100)) # P(C)
    v_loglik_constr = np.log(model.constrprob_Xv(posterior = True, algorithm = 'minimax_tilting', n = 100)) # P(C|Y)
                                 
    return (v_loglik_constr + v_loglik_constr_cond - v_loglik_unconstr) # P(Y|C)



def compute_loglik_meshdata(lengthscale_range, variance_range, constr = False, conditional = False):
    optimal_l = model.kernel.lengthscale[0]
    optimal_var = model.kernel.variance
    
    if constr:
        if conditional:
            X1, X2, Y = Create_meshdata(loglik_constr_cond, lengthscale_range, variance_range)                    
        else:
            X1, X2, Y = Create_meshdata(loglik_constr, lengthscale_range, variance_range)
    else:
        X1, X2, Y = Create_meshdata(loglik_unconstr, lengthscale_range, variance_range)
    
    # Reset model values
    model.kernel.variance = optimal_var
    model.kernel.lengthscale = [optimal_l]
    model.reset()
    
    return X1, X2, Y

In [123]:
# Optimize unconstrained
model.likelihood = 1
model.reset()
model.optimize(include_constraint = False, fix_likelihood = True)
print(model)

..Running optimization for unconstrained GP ... DONE - Total time: 0.031 seconds
----- GP model ----- 
 mean = 0 
 likelihood = 1 
 kernel: 
   type = RBF 
   input dim = 1 
   lenghtscale = [0.34571895] 
   variance = 0.2859095319707401 
 constraint: 
   f [20] 
   constr_likelihood = 1e-06 
---------------------


In [27]:
# Compute unconstrained likelihood
lengthscale_range = np.linspace(0.05, 1, 20)
variance_range = np.linspace(0.1, 3, 20)

X1, X2, Y = compute_loglik_meshdata(lengthscale_range, variance_range, constr = False)

contour_unconstr = go.Contour(
                                x = lengthscale_range, y = variance_range, z = Y, name = 'Unconstrained log-likelihood',
                                autocontour = False, contours=dict(start = -52, end = -50, size = 0.2),
                             )
max_unconstr = go.Scatter(x = [model.kernel.lengthscale[0]], y = [model.kernel.variance], mode = 'markers', name = 'current')

data = [contour_unconstr, max_unconstr]
layout = go.Layout(title = 'Unconstrained log-likelihood', xaxis=dict(title = 'lengthscale'), yaxis=dict(title = 'variance'))
fig = go.Figure(data = data, layout = layout)
pltlyoff.iplot(fig, filename='')
print('Optimal: {}, {}'.format(model.kernel.lengthscale[0], model.kernel.variance))

Optimal: 0.3457193292989496, 0.285910173068915


In [111]:
# Optimize constrained

#opt_args = {'maxiter': 10}
opt_args = {}

bound_lik = (0.01, 1)
bound_ker_var = (0.1, 3)
bound_ker_len = [(0.1, 2)]*1

bounds = [bound_lik] if bound_lik is not None else []
bounds = bounds + [bound_ker_var] + bound_ker_len
bounds = None
model._optimize_constrained(fix_likelihood = False, conditional = False, opt_method = 'differential_evolution', algorithm = 'minimax_tilting', n = 10, opt_args = opt_args)
print(model)

..Running optimization (differential_evolution) for constrained GP - max P(Y, C) ...

RRuntimeError: Error in nleq(l, u, L) : 
  Covariance matrix is ill-conditioned and method failed


In [120]:
print(model)

----- GP model ----- 
 mean = 0 
 likelihood = 0.04045665483075885 
 kernel: 
   type = RBF 
   input dim = 1 
   lenghtscale = [0.22006253] 
   variance = 0.27141486356042055 
 constraint: 
   f [20] 
   constr_likelihood = 1e-06 
---------------------


In [119]:
#model.likelihood = 0.1
model.reset()
model.constrprob_Xv(n = 10)

0.11845971356567243

In [ ]:
# Optimize constrained
model.constr_likelihood = 1E-6
model.kernel.lengthscale = [0.1]
model.kernel.variance = 0.5
model.reset()

opt_args = {'options' : {'maxtime ':10}}
opt_args = {}
model._optimize_constrained(fix_likelihood = True, opt_method = 'shgo', algorithm = 'minimax_tilting', n = 10, opt_args = opt_args)
print(model)

In [100]:
# Compute constrained likelihood
import time
#model.constr_likelihood = 1E-3
model.reset()
lengthscale_range = np.linspace(0.05, 2, 20)
variance_range = np.linspace(0.1, 3, 20)

t0 = time.time()
X1, X2, Y = compute_loglik_meshdata(lengthscale_range, variance_range, constr = True)
print('time ', time.time() - t0)

RRuntimeError: Error in nleq(l, u, L) : 
  Covariance matrix is ill-conditioned and method failed


In [80]:
contour_constr = go.Contour(
                                x = lengthscale_range, y = variance_range, z = Y, name = 'Constrained log-likelihood',
                                autocontour = False, contours=dict(start = -54, end = -50, size = 0.15),
                             )
max_constr = go.Scatter(x = [model.kernel.lengthscale[0]], y = [model.kernel.variance], mode = 'markers', name = 'current')

data = [contour_unconstr, max_unconstr, max_constr]
layout = go.Layout(title = 'Constrained log-likelihood, noise_var = ' + str(model.constr_likelihood), xaxis=dict(title = 'lengthscale'), yaxis=dict(title = 'variance'))
fig = go.Figure(data = data, layout = layout)
pltlyoff.iplot(fig, filename='')
print('Optimal: {}, {}'.format(model.kernel.lengthscale[0], model.kernel.variance))

Optimal: 1.2913355483858397, 0.31798331034722804


In [39]:
contour_constr = go.Contour(
                                x = lengthscale_range, y = variance_range, z = Y, name = 'Constrained log-likelihood',
                                autocontour = False, contours=dict(start = -54, end = -50, size = 0.15),
                             )
max_constr = go.Scatter(x = [model.kernel.lengthscale[0]], y = [model.kernel.variance], mode = 'markers', name = 'current')

data = [contour_unconstr, max_unconstr, max_constr]
layout = go.Layout(title = 'Constrained log-likelihood, noise_var = ' + str(model.constr_likelihood), xaxis=dict(title = 'lengthscale'), yaxis=dict(title = 'variance'))
fig = go.Figure(data = data, layout = layout)
pltlyoff.iplot(fig, filename='')
print('Optimal: {}, {}'.format(model.kernel.lengthscale[0], model.kernel.variance))

Optimal: 1.2913355483858397, 0.31798331034722804


In [81]:
# Compute constrained likelihood
import time
#model.constr_likelihood = 1E-3
model.reset()
lengthscale_range = np.linspace(0.05, 5, 30)
variance_range = np.linspace(0.1, 1, 30)

t0 = time.time()
X1, X2, Y = compute_loglik_meshdata(lengthscale_range, variance_range, constr = True, conditional = True)
print('time ', time.time() - t0)

time  15.433125734329224


In [83]:
contour_constr_cond = go.Contour(
                                x = lengthscale_range, y = variance_range, z = Y, name = 'Constrained log-likelihood',
                                autocontour = False, contours=dict(start = 45, end = 48, size = 0.5),
                             )
max_constr_cond = go.Scatter(x = [model.kernel.lengthscale[0]], y = [model.kernel.variance], mode = 'markers', name = 'current')

data = [contour_constr_cond, max_unconstr, max_constr, max_constr_cond]
layout = go.Layout(title = 'Constrained conditional log-likelihood, noise_var = ' + str(model.constr_likelihood), xaxis=dict(title = 'lengthscale'), yaxis=dict(title = 'variance'))
fig = go.Figure(data = data, layout = layout)
pltlyoff.iplot(fig, filename='')
print('Optimal: {}, {}'.format(model.kernel.lengthscale[0], model.kernel.variance))

Optimal: 1.2913355483858397, 0.31798331034722804


In [76]:
contour_constr_cond = go.Contour(
                                x = lengthscale_range, y = variance_range, z = Y, name = 'Constrained log-likelihood',
                                autocontour = False, contours=dict(start = 45, end = 51, size = 0.5),
                             )
max_constr_cond = go.Scatter(x = [model.kernel.lengthscale[0]], y = [model.kernel.variance], mode = 'markers', name = 'current')

data = [contour_constr_cond, max_unconstr, max_constr, max_constr_cond]
layout = go.Layout(title = 'Constrained conditional log-likelihood, noise_var = ' + str(model.constr_likelihood), xaxis=dict(title = 'lengthscale'), yaxis=dict(title = 'variance'))
fig = go.Figure(data = data, layout = layout)
pltlyoff.iplot(fig, filename='')
print('Optimal: {}, {}'.format(model.kernel.lengthscale[0], model.kernel.variance))

Optimal: 1.2913355483858397, 0.31798331034722804


## Test new alg bootstrap

In [124]:
# Optimize unconstrained
print(model)

----- GP model ----- 
 mean = 0 
 likelihood = 1 
 kernel: 
   type = RBF 
   input dim = 1 
   lenghtscale = [0.34571895] 
   variance = 0.2859095319707401 
 constraint: 
   f [20] 
   constr_likelihood = 1e-06 
---------------------


In [ ]:
# Draw from constraint dist
